In [1]:
import pdfplumber
import pytesseract
from PIL import Image
import pandas as pd
import re

# Se necessário, defina o caminho do Tesseract OCR no Windows
# pytesseract.pytesseract.tesseract_cmd = r"C:\Program Files\Tesseract-OCR\tesseract.exe"

def extrair_dados_pdf_ocr(caminho_pdf):
    dados = []

    with pdfplumber.open(caminho_pdf) as pdf:
        for i, pagina in enumerate(pdf.pages, start=1):
            print(f"Processando página {i}...")

            # Converter página em imagem
            imagem = pagina.to_image()
            imagem_pil = imagem.original  # Obter imagem PIL
            
            # Usar OCR para extrair texto da imagem
            texto = pytesseract.image_to_string(imagem_pil)
            
            # Tentar encontrar o número da nota fiscal
            num_nota_match = re.search(r'Nº\.:?\s*(\d{5})', texto)
            num_nota = num_nota_match.group(1) if num_nota_match else None

            # Tentar encontrar o valor total da nota fiscal
            valor_match = re.search(r'VALOR TOTAL DA NOTA\s*[R$\s]*([\d,.]+)', texto)
            valor_total = valor_match.group(1) if valor_match else None

            if num_nota and valor_total:
                dados.append([num_nota, valor_total])

    # Criar um DataFrame com os dados extraídos
    df = pd.DataFrame(dados, columns=["Número da Nota Fiscal", "Valor Total da Nota Fiscal"])
    return df

# Exemplo de uso
caminho_pdf = "Notas1.pdf"  # Substitua pelo caminho do seu arquivo PDF
df_resultado = extrair_dados_pdf_ocr(caminho_pdf)

print(df_resultado)

# Salvar os resultados em um arquivo CSV
df_resultado.to_csv("notas_fiscais_extraidas.csv", index=False)


Processando página 1...


TesseractNotFoundError: tesseract is not installed or it's not in your PATH. See README file for more information.